# download data

In [ ]:
import pandas as pd
import numpy as np
import urllib.request
import zipfile
import re
from geopy.distance import vincenty

In [ ]:
url = 'http://web.mta.info/developers/files/google_transit_supplemented.zip'
urllib.request.urlretrieve (url, "GTFS_nyc_Subway.zip")

('GTFS_nyc_Subway.zip', <http.client.HTTPMessage at 0x7f15974be990>)

In [ ]:
zip_ref = zipfile.ZipFile("GTFS_nyc_Subway.zip", 'r')
zip_ref.extractall("GTFS_nyc_Subway")
zip_ref.close()

# transit_service_analyst demo

##  Import libraries

In [ ]:
pip install geopandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.0 MB 20.0 MB/s 
     |████████████████████████████████| 6.3 MB 42.8 MB/s 
     |████████████████████████████████| 16.7 MB 528 kB/s 


In [ ]:
pip install transit-service-analyst

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
pip install pandera

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 120 kB 12.0 MB/s 


In [ ]:
%matplotlib inline
import pandas as pd
import geopandas as gpd
import transit_service_analyst as tsa
import plotly.express as px
import shapely.geometry
import numpy as np
import plotly.offline as pyo
#import nbformat
#import plotly.io as pio

## Create an instance of transit_service_analyst using a gtfs feed on file

In [ ]:
path = r'/content/GTFS_nyc_Subway/'
transit_analyst = tsa.load_gtfs(path,'20221001')

## The function get_lines_gdf() returns a GeodatFrame for each unique line by route, as determined by stop pattern. A trip_id representing each stop pattern is used as the unique ID and is called rep_trip_id. Show the first five rows: 

In [ ]:
transit_analyst.get_lines_gdf().head()

shape_id                                           geometry route_id  \
0  1..S03R  LINESTRING (-73.89858 40.88925, -73.89962 40.8...        1   
1  1..N03R  LINESTRING (-74.01366 40.70207, -74.01479 40.7...        1   
2  2..S08R  LINESTRING (-73.85062 40.90313, -73.85136 40.9...        2   
3  2..N08R  LINESTRING (-73.94764 40.63284, -73.94841 40.6...        2   
4  2..S01R  LINESTRING (-73.85062 40.90313, -73.85136 40.9...        2   

                                rep_trip_id                 service_id  \
0  ASP22GEN-1038-Saturday-00_000600_1..S03R  ASP22GEN-1038-Saturday-00   
1  ASP22GEN-1038-Saturday-00_007200_1..N03R  ASP22GEN-1038-Saturday-00   
2  ASP22GEN-2042-Saturday-00_001900_2..S08R  ASP22GEN-2042-Saturday-00   
3  ASP22GEN-2042-Saturday-00_013350_2..N08R  ASP22GEN-2042-Saturday-00   
4  ASP22GEN-2042-Saturday-00_029900_2..S01R  ASP22GEN-2042-Saturday-00   

                  trip_headsign  direction_id agency_id route_short_name  \
0                   South Ferry             1  MTA NYCT                1   
1     Van Cortlandt Park-242 St             0  MTA NYCT                1   
2  Flatbush Av-Brooklyn College             1  MTA NYCT                2   
3              Wakefield-241 St             0  MTA NYCT                2   
4  Flatbush Av-Brooklyn College             1  MTA NYCT                2   

             route_long_name  route_type  \
0  Broadway - 7 Avenue Local           1   
1  Broadway - 7 Avenue Local           1   
2           7 Avenue Express           1   
3           7 Avenue Express           1   
4           7 Avenue Express           1   

                                          route_desc  \
0  Trains operate between 242 St in the Bronx and...   
1  Trains operate between 242 St in the Bronx and...   
2  Trains operate between Wakefield-241 St, Bronx...   
3  Trains operate between Wakefield-241 St, Bronx...   
4  Trains operate between Wakefield-241 St, Bronx...   

                                        route_url route_color route_text_color  
0  http://web.mta.info/nyct/service/pdf/t1cur.pdf      EE352E              NaN  
1  http://web.mta.info/nyct/service/pdf/t1cur.pdf      EE352E              NaN  
2  http://web.mta.info/nyct/service/pdf/t2cur.pdf      EE352E              NaN  
3  http://web.mta.info/nyct/service/pdf/t2cur.pdf      EE352E              NaN  
4  http://web.mta.info/nyct/service/pdf/t2cur.pdf      EE352E              NaN

## Function to map line geometry

In [ ]:
# Functiont to plot lines
def create_line_map(df, name_col):
    if len(df) == 0:
        print ('Empty DF. No lines to map!')
    else:
        lats = []
        lons = []
        names = []

        for feature, name in zip(df.geometry, df[name_col]):
            if isinstance(feature, shapely.geometry.linestring.LineString):
                linestrings = [feature]
            elif isinstance(feature, shapely.geometry.multilinestring.MultiLineString):
                linestrings = feature.geoms
            else:
                continue
            for linestring in linestrings:
                x, y = linestring.xy
                lats = np.append(lats, y)
                lons = np.append(lons, x)
                names = np.append(names, [name]*len(y))
                lats = np.append(lats, None)
                lons = np.append(lons, None)
                names = np.append(names, None)


        fig = px.line_mapbox(lat=lats, lon=lons, hover_name=names,
                     mapbox_style="open-street-map", zoom=8)
        fig.show()

## Let's map one line for each route:

In [ ]:
# Call function to map routes
geo_df = transit_analyst.get_lines_gdf()
create_line_map(geo_df.groupby('route_id').first().reset_index(), 'route_short_name')

## The field transit_type is included so, for example, we can plot all routes

In [ ]:
not_bus = geo_df[geo_df['route_type']!=3]
create_line_map(not_bus, 'route_short_name')

## The function get_tph_by_line() returns a DataFrame with hourly frequencies for each rep_trip. Show the first 5 rows:

In [ ]:
transit_analyst.get_tph_by_line().head()

rep_trip_id  hour_0  hour_1  hour_2  hour_3  \
0  ASP22GEN-1038-Saturday-00_000600_1..S03R     3.0     3.0     3.0     3.0   
1  ASP22GEN-1038-Saturday-00_007200_1..N03R     0.0     3.0     3.0     3.0   
2  ASP22GEN-2042-Saturday-00_001900_2..S08R     3.0     3.0     3.0     3.0   
3  ASP22GEN-2042-Saturday-00_013350_2..N08R     0.0     0.0     3.0     3.0   
4  ASP22GEN-2042-Saturday-00_029900_2..S01R     0.0     0.0     0.0     0.0   

   hour_4  hour_5  hour_6  hour_7  hour_8  ...  hour_19  hour_20  hour_21  \
0     3.0     6.0     7.0     8.0     7.0  ...      8.0      7.0      8.0   
1     3.0     3.0     5.0     7.0     7.0  ...      8.0      7.0      8.0   
2     2.0     0.0     0.0     0.0     0.0  ...      0.0      0.0      0.0   
3     3.0     2.0     0.0     0.0     0.0  ...      0.0      0.0      0.0   
4     1.0     4.0     8.0     7.0     8.0  ...      5.0      5.0      5.0   

   hour_22  hour_23  hour_24  hour_25  hour_26  route_id  direction_id  
0      7.0      7.0      0.0      0.0      0.0         1             1  
1      7.0      8.0      7.0      1.0      0.0         1             0  
2      0.0      2.0      0.0      0.0      0.0         2             1  
3      0.0      1.0      3.0      3.0      0.0         2             0  
4      4.0      3.0      0.0      0.0      0.0         2             1  

[5 rows x 30 columns]

# Use get_tph_by_line() to get all rep_trips that have frequent service of 4 or more trips per hour during peak hours. 

In [ ]:
list_of_hours = ['hour_6', 'hour_7', 'hour_8', 'hour_15', 'hour_16', 'hour_17']
min_tph = 4
freq = transit_analyst.get_tph_by_line()
# create binary column for each hour
cols = []
for hour in list_of_hours:
    #print (len(freq))
    freq = freq[freq[hour]>=min_tph]

freq_rep_trips_gdf = geo_df[geo_df['rep_trip_id'].isin(freq['rep_trip_id'])]

print (f'There are {len(freq)} lines that have {min_tph} trips or more per hour.')


There are 33 lines that have 4 trips or more per hour.


In [ ]:
# map them
create_line_map(freq_rep_trips_gdf, 'route_short_name')

# The get_line_stops_gdf() function returns a GeoDataFrame consisting of the sequence of stops for each route returned by get_lines_gdf(). Use it and stops property to get the stops associated with the frequent routes. 

## The function get_tph_at_stops() function returns a DataFrame of total trips at each stop, independent of route. Let's use it to map stops by total number of trips for the AM peak:

In [ ]:
list_of_hours = ['hour_6', 'hour_7', 'hour_8']
trips_at_stops = transit_analyst.get_tph_at_stops()
trips_at_stops['am_trips'] = trips_at_stops['hour_6'] + trips_at_stops['hour_7'] + trips_at_stops['hour_8']

# join to stops
trips_at_stops = trips_at_stops.merge(transit_analyst.stops, how = 'left', on = 'stop_id')

# get the stops with the most trips:
max_trips = trips_at_stops['am_trips'].max()
test = trips_at_stops[trips_at_stops['am_trips']==max_trips]

if len(test)==1:
    stop_id = test['stop_id'].values[0]
    number_of_trips = test['am_trips'].values[0]
    print (f'stop_id {str(stop_id)} has the most AM trips with {number_of_trips}')
    



stop_id D43N has the most AM trips with 61.0


In [ ]:
# limit to 1000 stops
if len(trips_at_stops) > 1000:
    trips_at_stops.sort_values(by='am_trips', ascending=False, inplace = True)
    trips_at_stops = trips_at_stops.head(1000)

fig = px.scatter_mapbox(trips_at_stops,
                        lat=trips_at_stops['stop_lat'],
                        lon=trips_at_stops['stop_lon'],
                        hover_name="stop_id",
                        zoom=8,
                        mapbox_style="open-street-map",
                        size = 'am_trips')

fig.show()

# Let's use GeoPandas buffering function to buffer these stops.


In [ ]:
gdf = trips_at_stops.copy()
gdf = gpd.GeoDataFrame(gdf, geometry=gpd.points_from_xy(gdf.stop_lon, gdf.stop_lat))
# set initial geographic coordinate system.
gdf =gdf.set_crs(4326)
# need to switch to a projected system (state plane) to do buffer.
gdf = gdf.to_crs(2285)
gdf.geometry = gdf.geometry.buffer(1320)
# switch back to map
gdf = gdf.to_crs(4326)
gdf.set_index('stop_id', inplace = True)

fig = px.choropleth_mapbox(gdf,
                           geojson=gdf.geometry,
                           locations=gdf.index,
                           color="am_trips",
                           center={"lat": 40.758896, "lon": -73.985130},
                           mapbox_style="open-street-map",
                           zoom=8)
fig.show()
